# Goal: Recreate Gapminder's Bubble Chart*

![Gapminder](Gapminder.png)

*As much as possible...

## Import libraries

In [ ]:
import pandas as pd
import plotly.express as px
import plotly.graph_objs as go

## Get the data

In [ ]:
df = pd.read_csv('Gapminder-data.csv', sep=',')
df.head()

In [ ]:
df_info = pd.read_csv('Gapminder-info.csv', sep=',', index_col=0)
df_info

## Create the bubble chart

In [ ]:
df = df.sort_values(['Year', 'Population'], ascending=[True, False])

In [ ]:
color_map = {
    'Asia': '#ff798e', 
    'Europe': '#ffeb33', 
    'Africa': '#33dded',
    'Americas': '#98ef33'
}

In [ ]:
fig = px.scatter(
    df.query('Year==2020'), 
    x='Income', 
    y='Life expectancy', 
    color='Region',
    size='Population', 
    size_max=60,
    log_x=True, 
    hover_name='Country', 
    hover_data={c: False for c in df.columns},
    color_discrete_map=color_map,
    title='Gapminder<br><sup>Data from gapminder.org, CC-BY license</sup>'
)

In [ ]:
# Adjust markers
fig.update_traces(marker=dict(line=dict(color='black', width=0.8), opacity=1))
# Adjust figure layout
fig.update_layout(plot_bgcolor='white', 
                  font=dict(color='dimgray'), 
                  hoverlabel=dict(font_size=16))  #bgcolor='white', 
# Adjust axes and grid
fig.update_xaxes(showline=True, linewidth=1, linecolor='dimgray', gridcolor='lightgray', 
                 showspikes=True, spikecolor='dimgray', spikethickness=1)
fig.update_yaxes(showline=True, linewidth=1, linecolor='dimgray', gridcolor='lightgray', 
                 showspikes=True, spikecolor='dimgray', spikethickness=1)
fig.show()

## Add animation

In [ ]:
def gapminder_fig(xaxis='Income', yaxis='Life expectancy'):
    
    def background_year(year):
        """Return the dictionary containing a single position for the text that shows the year"""
        return dict(
            x=[df_info.loc[xaxis, 'Mid']],
            y=[df_info.loc[yaxis, 'Mid']],
            mode="text",
            showlegend=False,
            text=["{}".format(year)],
            textposition="middle center",
            textfont=dict(size=200, color="lightgray")
        )
    
    # Define the colors for the continents
    color_map = {
        'Asia': '#ff798e', 
        'Europe': '#ffeb33', 
        'Africa': '#33dded',
        'Americas': '#98ef33'
    }
    
    # Create the figure
    fig = px.scatter(
        df.query('Year>=2000'), 
        x=xaxis, 
        y=yaxis, 
        color='Region',
        size='Population', 
        size_max=60,
        log_x=df_info.loc[xaxis, 'LogScale'], 
        log_y=df_info.loc[yaxis, 'LogScale'], 
        hover_name='Country', 
        hover_data={c: False for c in df.columns},
        color_discrete_map=color_map,
        title='Gapminder<br><sup>Data from gapminder.org, CC-BY license</sup>',
        animation_frame='Year',
        animation_group='Country', 
        range_x=[df_info.loc[xaxis, 'Min'], df_info.loc[xaxis, 'Max']], 
        range_y=[df_info.loc[yaxis, 'Min'], df_info.loc[yaxis, 'Max']]
    )
    # Adjust markers
    fig.update_traces(marker=dict(line=dict(color='black', width=0.8), opacity=1))
    # Adjust figure layout
    fig.update_layout(plot_bgcolor='white', yaxis=dict(rangemode='tozero'), font=dict(color='dimgray'), 
                      hoverlabel=dict(font_size=16)) 
    fig.update_layout(autosize=False, width=800, height=600)
    
    # Adjust axes and grid
    fig.update_xaxes(showline=True, linewidth=1, linecolor='dimgray', gridcolor='lightgray', 
                     showspikes=True, spikecolor='dimgray', spikethickness=1)
    fig.update_yaxes(showline=True, linewidth=1, linecolor='dimgray', gridcolor='lightgray', 
                     showspikes=True, spikecolor='dimgray', spikethickness=1)
    
    # Show the year in the background
    frame_year = fig.frames[0].name
    fig.add_trace(go.Scatter(background_year(frame_year)))
    fig.data = (fig.data[-1], ) + fig.data[:-1]
    for frame in fig.frames:
        frame.data = (background_year(frame.name), ) + frame.data
    # Remove year from the slider
    fig.layout.sliders[0].currentvalue.update({'visible': False})
    
    # Add annotations to the axes
    fig.add_annotation(xref='x domain', yref='y domain', x=1, y=0, 
                       text=df_info.loc[xaxis, 'Meaning'], showarrow=False, align='right')
    fig.add_annotation(xref='x domain', yref='y domain', x=0, y=1, 
                       text=df_info.loc[yaxis, 'Meaning'], showarrow=False, valign='top', textangle=-90)
    
    # Emphasize the selected point (hold shift for selecting multiple countries)
    fig.update_layout(clickmode='event+select')
    
    return fig
fig = gapminder_fig()
fig.show()

## Make axes choice interactive

In [ ]:
import numpy as np
from jupyter_dash import JupyterDash
from dash import dcc, html
from dash.dependencies import Input, Output
import json

- Dash html components: https://dash.plotly.com/dash-html-components
- Dash core components: https://dash.plotly.com/dash-core-components

In [ ]:
external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']
app = JupyterDash(__name__, external_stylesheets=external_stylesheets)
attributes = ['Income', 'Life expectancy', 'Fertility', 'Child mortality']
app.layout = html.Div([
    html.H1(
        'Interactive data visualization', 
        style={'fontSize': 50}#, 'text-align': 'center'}
    ),
    dcc.Graph(
        id='plot', 
        figure=gapminder_fig()
    ),
    html.Div([
        html.P('X axis'),
        dcc.Dropdown(
            id='dropdown_x',
            options=[{'label': a, 'value': a} for a in attributes],
            value='Income',
            clearable=False
        )],
        style={'width': '200px', 'display': 'inline-block', 'padding-right': '10px'}
    ),
    html.Div([
        html.P('Y axis'),
        dcc.Dropdown(
            id='dropdown_y',
            options=[{'label': a, 'value': a} for a in attributes],
            value='Life expectancy',
            clearable=False
        )],
        style={'width': '200px', 'display': 'inline-block'}
    ),
],
    style={'width': '800px', 'margin': '0 auto'}
)

@app.callback(
    Output('plot', 'figure'), 
    [Input('dropdown_x', 'value'), Input('dropdown_y', 'value')])
def update_plot(value_x, value_y):
    return gapminder_fig(xaxis=value_x, yaxis=value_y)

In [ ]:
app.run_server(debug=True, mode='inline')

## Retreive information from selected points

In [ ]:
external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']
app = JupyterDash(__name__, external_stylesheets=external_stylesheets)
attributes = ['Income', 'Life expectancy', 'Fertility', 'Child mortality']
app.layout = html.Div([
    html.H1(
        'Interactive data visualization', 
        style={'fontSize': 50}#, 'text-align': 'center'}
    ),
    dcc.Graph(
        id='plot', 
        figure=gapminder_fig()
    ),
    html.Div([
        html.P('X axis'),
        dcc.Dropdown(
            id='dropdown_x',
            options=[{'label': a, 'value': a} for a in attributes],
            value='Income',
            clearable=False
        )],
        style={'width': '200px', 'display': 'inline-block', 'padding-right': '10px'}
    ),
    html.Div([
        html.P('Y axis'),
        dcc.Dropdown(
            id='dropdown_y',
            options=[{'label': a, 'value': a} for a in attributes],
            value='Life expectancy',
            clearable=False
        )],
        style={'width': '200px', 'display': 'inline-block'}
    ),
    html.Div([
        html.P('Selected countries'),
        dcc.Textarea(
            id='text',
            value='',
            contentEditable=False,
            draggable=False,
            style={'width': '100%', 'height': '400px'}
        )],
        style={'padding-top': '10px'}
    ),
],
    style={'width': '800px', 'margin': '0 auto'}
)

@app.callback(
    Output('plot', 'figure'), 
    [Input('dropdown_x', 'value'), Input('dropdown_y', 'value')])
def update_plot(value_x, value_y):
    return gapminder_fig(xaxis=value_x, yaxis=value_y)

@app.callback(
    Output('text', 'value'),
    Input('plot', 'selectedData'))
def print_value(selected_data):
    return json.dumps(selected_data, indent=2) 

In [ ]:
app.run_server(debug=True)